Error test of Monte Carlo simulation

In [ ]:
import numpy as np
import scipy.stats
from mpl_toolkits.mplot3d import Axes3D
import matplotlib.pyplot as plt
from IPython.core.display import display, HTML
import json

BS analytical solution

In [2]:
def get_bs_price(s, sigma, t, r, k):
    y1 = (np.log(s/k) + (r + 0.5*(sigma**2))* t) / (sigma * np.sqrt(t))
    y2 = (np.log(s/k) + (r - 0.5*(sigma**2)) * t) / (sigma * np.sqrt(t))
    cdf1 = scipy.stats.norm.cdf(y1)
    cdf2 = scipy.stats.norm.cdf(y2)
    price = s * cdf1 - np.exp(-r * t) * k * cdf2
    return price

MC method

In [3]:
def call_MS(S0, sigma, T, r, K, iterations):
        
    option_price=np.zeros([iterations,2])
    rand=np.random.normal(0,1,[1,iterations])
    #find the stick price by using MC method
    stock_price=S0*np.exp(T*(r-0.5*sigma**2)+sigma*np.sqrt(T)*rand)
        
    #Find the intrisic value
    option_price[:,1]=stock_price-K
    
    #plt.plot(option_price[:150,1])
    #plt.title('MC model')
    #plt.ylabel('Option price')
    #plt.xlabel('Iterations')
    #plt.grid(True)
    #plt.show()
        
    average=np.sum(np.amax(option_price,axis=1))/float(iterations)
        #consider the time value
    price=np.exp(-1.0*r*T)*average
    return price

Parameters value

In [4]:
T = 0.3
S_0 = 105
r = 0.1
sigma = 0.2
K = 100
iterations=10000

test if MC method work

In [5]:
print(call_MS(S_0, sigma, T, r, K, iterations))

9.35724546875


In [6]:
iterations = 900

sigma = 0.5
K = 100;
r = 0.05;

T = np.linspace(0.01, 2, num=100)
S_0= np.linspace(K * 0.1, K*2, num=100)

X,Y = np.meshgrid(T,S_0)
prices = get_bs_price(Y, sigma, X, r, K)
means = np.zeros(prices.shape)

In [ ]:
Calculate all the values in the range and record the runtime

In [7]:
%%time
for i in range(len(S_0)):
    for j in range(len(T)):
        means[i][j]=call_MS(S_0[i], sigma, T[j], r, K, iterations)      

CPU times: user 911 ms, sys: 6.79 ms, total: 918 ms
Wall time: 921 ms


3D plot class 

In [8]:
def plot3D(X, Y, Z, height=600, xlabel = "Sigma", ylabel = "K", zlabel = "Option Price", initialCamera = None):

    options = {
        "width": "100%",
        "style": "surface",
        "showPerspective": True,
        "showGrid": True,
        "showShadow": False,
        "keepAspectRatio": True,
        "height": str(height) + "px"
    }
    if initialCamera:
        options["cameraPosition"] = initialCamera
        
    data = [ {"x": X[y,x], "y": Y[y,x], "z": Z[y,x]} for y in range(X.shape[0]) for x in range(X.shape[1]) ]
    visCode = r"""
       <link href="https://cdnjs.cloudflare.com/ajax/libs/vis/4.21.0/vis.min.css" type="text/css" rel="stylesheet" />
       <script src="https://cdnjs.cloudflare.com/ajax/libs/vis/4.21.0/vis.min.js"></script>
       <div id="pos" style="top:0px;left:0px;position:absolute;"></div>
       <div id="visualization"></div>
       <script type="text/javascript">
        var data = new vis.DataSet();
        data.add(""" + json.dumps(data) + """);
        var options = """ + json.dumps(options) + """;
        var container = document.getElementById("visualization");
        var graph3d = new vis.Graph3d(container, data, options);
        graph3d.on("cameraPositionChange", function(evt)
        {
            elem = document.getElementById("pos");
            elem.innerHTML = "H: " + evt.horizontal + "<br>V: " + evt.vertical + "<br>D: " + evt.distance;
        });
       </script>
    """
    htmlCode = "<iframe srcdoc='"+visCode+"' width='100%' height='" + str(height) + "px' style='border:0;' scrolling='no'> </iframe>"
    display(HTML(htmlCode))
        

In [9]:
X, Y = np.meshgrid(np.linspace(0,100,100),np.linspace(0,100,100))
Z = prices
print(np.mean(Z))
plot3D(X, Y, Z)

35.078598123


In [49]:
X, Y = np.meshgrid(np.linspace(0,100,100),np.linspace(0,100,100))
Z = means
plot3D(X, Y, Z)

In [10]:
errors=abs(means-prices)
print(np.mean(errors))
print(np.std(errors))
print(np.amax(errors))
X, Y = np.meshgrid(np.linspace(0,100,100),np.linspace(0,100,100))
Z = errors 
plot3D(X, Y, Z)

1.18714725148
1.57268559639
15.125993367


In [11]:
T = 1
S_0 = 100;
r = 0.05;

sigma = np.linspace(0.01, 0.7, num=100)
K = np.linspace(S_0 * 0.1, S_0*2, num=100)

X,Y = np.meshgrid(K, sigma)
prices2 = get_bs_price(S_0, Y, T, r, X)
means2 = np.zeros(prices.shape)


X, Y = np.meshgrid(np.linspace(0,100,100),np.linspace(0,100,100))
Z = prices2
print(np.mean(Z))
plot3D(X, Y, Z)

27.3367838834


In [61]:
%%time
for i in range(len(sigma)):
    for j in range(len(K)):
        means2[i][j]=call_MS(S_0, sigma[i], T, r, K[j], iterations) 

CPU times: user 923 ms, sys: 6.58 ms, total: 930 ms
Wall time: 934 ms


In [62]:
X, Y = np.meshgrid(np.linspace(0,100,100),np.linspace(0,100,100))
Z = means2
plot3D(X, Y, Z)

In [63]:
errors2=abs(means2-prices2)
print(np.mean(errors2))
print(np.std(errors2))
print(np.amax(errors2))
X, Y = np.meshgrid(np.linspace(0,100,100),np.linspace(0,100,100))
Z = errors2
plot3D(X, Y, Z)

0.714460434567
0.889889083863
7.88674324532


In [12]:
S_0 = 100;
sigma=0.05
K=100

T = np.linspace(0.01, 2, num=100)
r = np.linspace(0.01, 0.5, num=100)

X,Y = np.meshgrid(r, T)
prices3 = get_bs_price(S_0, sigma, Y, X, K)
means3 = np.zeros(prices3.shape)


X, Y = np.meshgrid(np.linspace(0,100,100),np.linspace(0,100,100))
Z = prices3
print(np.mean(Z))
plot3D(X, Y, Z)

20.9083895881


In [57]:
%%time
for i in range(len(T)):
    for j in range(len(r)):
        means3[i][j]=call_MS(S_0, sigma, T[i], r[j], K, iterations) 

CPU times: user 890 ms, sys: 5.08 ms, total: 895 ms
Wall time: 896 ms


In [58]:
errors3=abs(means3-prices3)
print(np.mean(errors3))
print(np.std(errors3))
print(np.amax(errors3))
X, Y = np.meshgrid(np.linspace(0,100,100),np.linspace(0,100,100))
Z = means3
plot3D(X, Y, Z)

0.121850412339
0.106557916013
0.758920511789


In [59]:
X, Y = np.meshgrid(np.linspace(0,100,100),np.linspace(0,100,100))
print(np.mean(errors3))
print(np.std(errors3))
print(np.amax(errors3))
Z = errors3
plot3D(X, Y, Z)

0.121850412339
0.106557916013
0.758920511789


03 Mar 2018